In [ ]:
!ppython -m spacy download en_core_web_sm
!pip install simpletransformers


/bin/bash: ppython: command not found
     |████████████████████████████████| 221 kB 8.2 MB/s 
     |████████████████████████████████| 1.2 MB 36.3 MB/s 
     |████████████████████████████████| 542 kB 43.8 MB/s 
     |████████████████████████████████| 43 kB 1.6 MB/s 
     |████████████████████████████████| 3.3 MB 44.7 MB/s 
     |████████████████████████████████| 7.9 MB 44.6 MB/s 
     |████████████████████████████████| 1.8 MB 47.6 MB/s 
     |████████████████████████████████| 2.6 MB 35.7 MB/s 
     |████████████████████████████████| 76 kB 3.7 MB/s 
     |████████████████████████████████| 124 kB 51.6 MB/s 
     |████████████████████████████████| 636 kB 35.1 MB/s 
     |████████████████████████████████| 895 kB 34.0 MB/s 
     |████████████████████████████████| 138 kB 50.3 MB/s 
     |████████████████████████████████| 97 kB 4.7 MB/s 
     |████████████████████████████████| 177 kB 49.7 MB/s 
     |████████████████████████████████| 133 kB 42.8 MB/s 
     |████████████████████████████████| 6

     |████████████████████████████████| 120 kB 8.3 MB/s 
  Attempting uninstall: ipykernel
    Found existing installation: ipykernel 6.0.3
    Uninstalling ipykernel-6.0.3:
      Successfully uninstalled ipykernel-6.0.3
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
jupyter-console 5.2.0 requires prompt-toolkit<2.0.0,>=1.0.0, but you have prompt-toolkit 3.0.19 which is incompatible.
google-colab 1.0.0 requires ipykernel~=4.10, but you have ipykernel 5.5.5 which is incompatible.
google-colab 1.0.0 requires ipython~=5.5.0, but you have ipython 7.25.0 which is incompatible.
google-colab 1.0.0 requires requests~=2.23.0, but you have requests 2.26.0 which is incompatible.


In [ ]:
import ipykernel
ipykernel.version_info

(5, 5, 5)

In [ ]:
from google.colab import drive
drive.mount("/content/drive", force_remount=True)



Mounted at /content/drive


In [ ]:
chemincorpus = "/content/drive/MyDrive/Stage Defense/Corpus/"
cheminw2v = chemincorpus + 'W2V_EN_mentions_Defense.csv'
cheminbow = chemincorpus + 'BoW_EN_mentions_Defense.csv'
cheminfeatures = chemincorpus +"features_EN_contexte_Defense.csv"


In [ ]:



import numpy as np
import pandas as pd

import matplotlib.pyplot as plt

from sklearn.metrics import classification_report
from sklearn.model_selection import train_test_split, cross_val_score, cross_val_predict
from sklearn.svm import LinearSVC,SVC
from sklearn.model_selection import KFold, StratifiedKFold
from sklearn.utils.class_weight import compute_class_weight



In [ ]:

from simpletransformers.classification import ClassificationModel, ClassificationArgs
import logging

In [ ]:

import spacy
nlp = spacy.load('en')

Fonctions utiles

In [ ]:
def equilibre_classes(X,y,threshold=None):
  '''Retire aléatoirement des exemples des classes surnnuméraires, à la fois dans X et dans y
  Renvoie X et y avec toutes les classes ayant le meme nombre d'exemple que la classe minoritaire'''
  dicoclasses = {k:v for k,v in zip(*np.unique(y, return_counts=True))}
  print("avant",dicoclasses)
  mini = min(dicoclasses.values())
  if threshold:
    mini = threshold
  while any((v >mini for v in dicoclasses.values())):
    
    for cat in dicoclasses:
      
      if dicoclasses[cat] > mini:
        nb_hasard = np.random.choice(np.where(y==cat)[0],1)
        X = np.delete(X,nb_hasard, axis=0)
        y = np.delete(y,nb_hasard, axis=0)
        dicoclasses[cat]-=1

  print("apres",dicoclasses)
  return X,y
  #for i in range(len(X)):


In [ ]:
def conversion_classes_num(y,convert,reverse_conv=False):
  if reverse_conv:
    convert = {v:k for k,v in convert.items()}
  for i in range(len(y)):
    y[i] = convert[y[i]]
  return y

In [ ]:
def validation_croisee_roberta(X,y,convert,n_epochs,n_splits=5):
  kf = StratifiedKFold(n_splits=n_splits, random_state=None, shuffle=True)
  y_pred,y_true = [], []
  for train_index, test_index in kf.split(X,y):
    #print("TRAIN:", train_index, "TEST:", test_index)
    
    X_train, X_test = X[train_index], X[test_index]
    y_train, y_test = y[train_index], y[test_index]
    y_train, y_test = conversion_classes_num(y_train,convert),conversion_classes_num(y_test,convert)
    df_train = pd.DataFrame(zip(X_train,y_train), columns = ["text","labels"])
    df_test = pd.DataFrame(zip(X_test,y_test), columns = ["text","labels"])
    #print(df_train)
    print(convert.values(), np.unique(y_train))
    weights = compute_class_weight('balanced',list(convert.values()),y_train)
    model_args = ClassificationArgs(num_train_epochs=n_epochs,overwrite_output_dir=True)
    model = ClassificationModel(
      'roberta',
      'roberta-base',
      weight=weights.tolist(),
      num_labels = len(convert),
      args=model_args) 
    
    model.train_model(df_train)
    predictions, raw_outputs = model.predict(X_test.tolist())
    y_pred.extend(predictions)
    y_true.extend(y_test)
  return y_pred,y_true

In [ ]:
def liste_lemmes_predicat(phrase,lemme=True,
                          pos_filtre=['VERB','ADJ','ADV','INTJ','NOUN'],
                          lemme_filtre = ['ville','défense']):
    doc = nlp(phrase)
    liste_lemmes = []
    for tok in doc:
      if tok.text == 'ville':
        tete = tok.head
        if tete.pos_ != 'VERB' or len(list(tete.subtree))<3:
          tete = tete.head
        #print(tete,tete.pos_, list(tete.subtree), phrase, sep=' | ')
        for elem in tete.subtree:
          if elem.pos_ in pos_filtre and elem.lemma_  not in lemme_filtre:
            if lemme:
              liste_lemmes.append(elem.lemma_.lower())
            else:
              liste_lemmes.append(elem.text)
    return liste_lemmes

Chargement des données

In [ ]:
dfbow = pd.read_csv(cheminbow, sep=",",index_col=0)
dfw2v = pd.read_csv(cheminw2v, sep=",",index_col=0)
dffeatures = pd.read_csv(cheminfeatures, sep=",",index_col=0)

In [ ]:
chemindata = chemincorpus+"Toutes_mentions_Defense_EN.csv"

In [ ]:
annotations = pd.read_csv(chemindata,sep=",", index_col=0, keep_default_na=False,na_values=["NA"])
#annotations = annotations.loc[:,"cible_contexte":"positionnement_contexte"]
annotations = annotations.fillna("NA")

In [ ]:
for col_name in annotations:
  annotations[col_name] = annotations[col_name].str.strip()

In [ ]:
annotations = annotations.loc[dfbow.index,:]
annotations.cible_contexte = annotations.cible_contexte.str.strip()
annotations.loc[annotations[annotations.cible_contexte=="administration politique"].index,'cible_contexte'] = "administration"
annotations.loc[annotations[annotations.cible_contexte=="quotidien"].index,'cible_contexte'] = "vie quotidienne"
annotations.loc[annotations[annotations.cible_contexte=="évenement"].index,'cible_contexte'] = "événement"

In [ ]:
annotations.cible_contexte.unique()

array(['urbanisme', 'NA', 'économie', 'événement', 'tourisme',
       'immobilier', 'vie quotidienne', 'administration'], dtype=object)

In [ ]:

X_bow_contexte = dfbow.iloc[:,160:]

In [ ]:

X_w2v_contexte = dfw2v.iloc[:,300:]

# Predictions Contexte

## Cible Contexte

In [ ]:
np.unique(annotations.cible_contexte)

array(['NA', 'administration', 'immobilier', 'tourisme', 'urbanisme',
       'vie quotidienne', 'économie', 'événement'], dtype=object)


###  RoBERTa

Na Vs Non-NA

In [ ]:

logging.basicConfig(level=logging.INFO)
transformers_logger = logging.getLogger("transformers")
transformers_logger.setLevel(logging.WARNING)

Validation croisée

In [ ]:
X_contexte = dffeatures.contexte.to_numpy()
y_cible_na = np.where(y_cible_c != 'NA', "non_na", y_cible_c)


In [ ]:
n_splits = 5
n_epochs = 15

In [ ]:
convert = {'NA':0,"non_na":1}
y_pred,y_true = validation_croisee_roberta(X_contexte,y_cible_na,convert,n_epochs,n_splits)

INFO:filelock:Lock 139955900563216 acquired on /root/.cache/huggingface/transformers/733bade19e5f0ce98e6531021dd5180994bb2f7b8bd7e80c7968805834ba351e.35205c6cfc956461d8515139f0f8dd5d207a2f336c0c3a83b4bc8dca3518e37b.lock


dict_values([0, 1]) [0 1]


Downloading:   0%|          | 0.00/481 [00:00<?, ?B/s]

INFO:filelock:Lock 139955900563216 released on /root/.cache/huggingface/transformers/733bade19e5f0ce98e6531021dd5180994bb2f7b8bd7e80c7968805834ba351e.35205c6cfc956461d8515139f0f8dd5d207a2f336c0c3a83b4bc8dca3518e37b.lock
INFO:filelock:Lock 139955876318608 acquired on /root/.cache/huggingface/transformers/51ba668f7ff34e7cdfa9561e8361747738113878850a7d717dbc69de8683aaad.c7efaa30a0d80b2958b876969faa180e485944a849deee4ad482332de65365a7.lock


Downloading:   0%|          | 0.00/501M [00:00<?, ?B/s]

...

Running Epoch 13 of 15:   0%|          | 0/46 [00:00<?, ?it/s]

Running Epoch 14 of 15:   0%|          | 0/46 [00:00<?, ?it/s]

INFO:simpletransformers.classification.classification_model: Training of roberta model complete. Saved to outputs/.
INFO:simpletransformers.classification.classification_utils: Converting to features started. Cache is not used.


  0%|          | 0/90 [00:00<?, ?it/s]

  0%|          | 0/12 [00:00<?, ?it/s]

In [ ]:
y_true = conversion_classes_num(y_true,convert,reverse_conv=True)
y_pred = conversion_classes_num(y_pred,convert,reverse_conv=True)
report = classification_report(y_true,y_pred)

In [ ]:
print(report)

              precision    recall  f1-score   support

          NA       0.78      0.70      0.74       152
      non_na       0.86      0.90      0.88       301

    accuracy                           0.83       453
   macro avg       0.82      0.80      0.81       453
weighted avg       0.83      0.83      0.83       453



### Extraction des NA

In [ ]:
index_na = annotations[annotations.cible_contexte == 'NA'].index
index_non_na = annotations[annotations.cible_contexte != 'NA'].index

### Autres cibles

In [ ]:
def reequilibre_classes(X,y,cible_support):
  
  classes,counts = np.unique(np.array([label  for labels in y for label in labels]),return_counts=True)
  dico_counts = {classe: count for classe,count in zip(classes,counts)}
  dico_counts = dict(sorted(dico_counts.items(),key=lambda x:x[1] , reverse=True))
  print("avant", dico_counts)
  #print(X)

  new_X,new_y = [], []
  if not isinstance(X,list):
    X= X.tolist()
  nb_sup,nb_add = 0,0
  nb_total = len(X)
  for label in dico_counts:
    print(label,"avant", dico_counts)
    while dico_counts[label]  < cible_support   or dico_counts[label]  > cible_support:
      i = random.randint(0,len(y)-1)
      labels = y[i]
      if label not in labels : continue
      if dico_counts[label] < cible_support :
        for lab in labels:
          dico_counts[lab] +=1
        X.append(X[i])
        y.append(y[i])
        nb_add +=1
      elif dico_counts[label] > cible_support :
        if any((dico_counts[lab] < cible_support-5 for lab in labels) ): continue
        for lab in labels:
          dico_counts[lab] -=1
        del X[i]
        del y[i]
        nb_sup+=1
    
    print(label,"après", dico_counts)

  classes,counts = np.unique(np.array([label  for labels in y for label in labels]),return_counts=True)
  dico_counts = {classe: count for classe,count in zip(classes,counts)}
  print(f"exemples avant : {nb_total}", f"ajoutés : {nb_add}", f"supprimés : {nb_sup}", f"exemples après : {len(X)}", sep = " | ")


  new_dico_counts =   {classe: count for classe,count in zip(*np.unique(np.array([label  for labels in new_y for label in labels]),return_counts=True))}
  print("a la fin",new_dico_counts)
  return X,y

### RoBERTa

In [ ]:
X_cible = dffeatures.loc[index_non_na,'contexte'].to_numpy()
y_cible = annotations.loc[index_non_na,'cible_contexte'].to_numpy()

In [ ]:
n_splits = 5
n_epochs = 15
convert = {'économie':0, 'vie quotidienne':1, 'urbanisme':2, 'événement':3,
       'administration':4, 'tourisme':5,  'immobilier':6}
#y_cible = conversion_classes_num(y_cible,convert)

In [ ]:
y_pred, y_true = validation_croisee_roberta(X_cible,y_cible,convert,n_epochs,n_splits)

dict_values([0, 1, 2, 3, 4, 5, 6]) [0 1 2 3 4 5 6]


Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['lm_head.dense.weight', 'lm_head.decoder.weight', 'lm_head.layer_norm.weight', 'lm_head.layer_norm.bias', 'lm_head.bias', 'lm_head.dense.bias']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.out_proj.weight', 'classifier.out_proj.bias', 'classifier.dense.bias', 'classifier.de

  0%|          | 0/240 [00:00<?, ?it/s]

INFO:simpletransformers.classification.classification_utils: Saving features into cached file cache_dir/cached_train_roberta_128_7_2


Epoch:   0%|          | 0/15 [00:00<?, ?it/s]

...

Running Epoch 13 of 15:   0%|          | 0/31 [00:00<?, ?it/s]

Running Epoch 14 of 15:   0%|          | 0/31 [00:00<?, ?it/s]

INFO:simpletransformers.classification.classification_model: Training of roberta model complete. Saved to outputs/.
INFO:simpletransformers.classification.classification_utils: Converting to features started. Cache is not used.


  0%|          | 0/60 [00:00<?, ?it/s]

  0%|          | 0/8 [00:00<?, ?it/s]

In [ ]:
y_true = conversion_classes_num(y_true,convert,reverse_conv=True)
y_pred = conversion_classes_num(y_pred,convert,reverse_conv=True)
report = classification_report(y_true,y_pred)

In [ ]:
print(report)

                 precision    recall  f1-score   support

 administration       0.20      0.14      0.17         7
     immobilier       0.76      0.74      0.75        34
       tourisme       0.44      0.48      0.46        23
      urbanisme       0.79      0.77      0.78        44
vie quotidienne       0.25      0.20      0.22        10
       économie       0.64      0.60      0.62        57
      événement       0.87      0.92      0.89       126

       accuracy                           0.74       301
      macro avg       0.56      0.55      0.56       301
   weighted avg       0.73      0.74      0.74       301



## Temporalité

Temporalité RoBERTa

In [ ]:
X_phrase = dffeatures.loc[index_non_na,"contexte"].to_numpy()
y_tempo = annotations.loc[index_non_na,'temporalité'].to_numpy()

In [ ]:
n_splits = 5
n_epochs = 15
convert = {'passé':0, 'présent':1, 'futur':2,}

In [ ]:
y_tempo = annotations.loc[index_non_na,'temporalité'].to_numpy()

#y_cible = conversion_classes_num(y_cible,convert)

In [ ]:
y_pred,y_true = validation_croisee_roBERTa(X_phrase,y_tempo,convert,n_epochs, n_splits)



dict_values([0, 1, 2]) [0 1 2]


Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['lm_head.dense.weight', 'lm_head.decoder.weight', 'lm_head.layer_norm.weight', 'lm_head.layer_norm.bias', 'lm_head.bias', 'lm_head.dense.bias']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.out_proj.weight', 'classifier.out_proj.bias', 'classifier.dense.bias', 'classifier.de

  0%|          | 0/240 [00:00<?, ?it/s]

INFO:simpletransformers.classification.classification_utils: Saving features into cached file cache_dir/cached_train_roberta_128_3_2


Epoch:   0%|          | 0/15 [00:00<?, ?it/s]

...

Running Epoch 13 of 15:   0%|          | 0/31 [00:00<?, ?it/s]

Running Epoch 14 of 15:   0%|          | 0/31 [00:00<?, ?it/s]

INFO:simpletransformers.classification.classification_model: Training of roberta model complete. Saved to outputs/.
INFO:simpletransformers.classification.classification_utils: Converting to features started. Cache is not used.


  0%|          | 0/60 [00:00<?, ?it/s]

  0%|          | 0/8 [00:00<?, ?it/s]

In [ ]:
y_true = conversion_classes_num(y_true,convert,reverse_conv=True)
y_pred = conversion_classes_num(y_pred,convert,reverse_conv=True)
report = classification_report(y_true,y_pred)

In [ ]:
print(report)

              precision    recall  f1-score   support

       futur       0.36      0.28      0.31        18
       passé       0.61      0.62      0.62        40
     présent       0.89      0.90      0.89       243

    accuracy                           0.82       301
   macro avg       0.62      0.60      0.61       301
weighted avg       0.82      0.82      0.82       301



## Polarité

RoBERTa

In [ ]:
X_phrase = dffeatures.loc[index_non_na,"contexte"].to_numpy()
y_pola_c = annotations.loc[index_non_na,'polarité_contexte']

In [ ]:
n_splits = 5
n_epochs = 15
convert = {'négatif':0, 'neutre':1, 'positif':2}

In [ ]:
y_pred,y_true = validation_croisee_roberta(X_phrase,y_pola_c.to_numpy(),convert,n_epochs, n_splits)

dict_values([0, 1, 2]) [0 1 2]


Downloading:   0%|          | 0.00/481 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/501M [00:00<?, ?B/s]

Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['lm_head.decoder.weight', 'lm_head.dense.bias', 'lm_head.dense.weight', 'lm_head.layer_norm.bias', 'lm_head.bias', 'lm_head.layer_norm.weight']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.out_proj.bias', 'classifier.dense.weight', 'classifier.dense.bias', 'classifier.out_p

Downloading:   0%|          | 0.00/899k [00:00<?, ?B/s]

...

Running Epoch 12 of 15:   0%|          | 0/31 [00:00<?, ?it/s]

Running Epoch 13 of 15:   0%|          | 0/31 [00:00<?, ?it/s]

Running Epoch 14 of 15:   0%|          | 0/31 [00:00<?, ?it/s]

  0%|          | 0/60 [00:00<?, ?it/s]

  0%|          | 0/8 [00:00<?, ?it/s]

In [ ]:
y_true = conversion_classes_num(y_true,convert,reverse_conv=True)
y_pred = conversion_classes_num(y_pred,convert,reverse_conv=True)
report = classification_report(y_true,y_pred)

In [ ]:
print(report)

              precision    recall  f1-score   support

      neutre       0.56      0.76      0.64        50
     négatif       0.66      0.68      0.67        31
     positif       0.77      0.48      0.59        50

    accuracy                           0.63       131
   macro avg       0.66      0.64      0.63       131
weighted avg       0.66      0.63      0.63       131



## Positionnement contexte

In [ ]:
X_phrase = dffeatures.loc[index_non_na,"contexte"].to_numpy()
y_position = annotations.loc[index_non_na,'positionnement_contexte']

In [ ]:
n_splits = 5
n_epochs = 15
convert = {'pris en charge':0, 'cité':1, 'attribué':2}

In [ ]:
y_pred,y_true = validation_croisee_roberta(X_phrase,y_position.to_numpy(),convert,n_epochs, n_splits)

/usr/local/lib/python3.7/dist-packages/sklearn/model_selection/_split.py:667: UserWarning: The least populated class in y has only 2 members, which is less than n_splits=5.
  % (min_groups, self.n_splits)), UserWarning)


dict_values([0, 1, 2]) [0 1 2]


Some weights of the model checkpoint at roberta-base were not used when initializing RobertaForSequenceClassification: ['lm_head.decoder.weight', 'lm_head.dense.bias', 'lm_head.dense.weight', 'lm_head.layer_norm.bias', 'lm_head.bias', 'lm_head.layer_norm.weight']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.out_proj.bias', 'classifier.dense.weight', 'classifier.dense.bias', 'classifier.out_p

  0%|          | 0/240 [00:00<?, ?it/s]

Epoch:   0%|          | 0/15 [00:00<?, ?it/s]

...

Running Epoch 12 of 15:   0%|          | 0/31 [00:00<?, ?it/s]

Running Epoch 13 of 15:   0%|          | 0/31 [00:00<?, ?it/s]

Running Epoch 14 of 15:   0%|          | 0/31 [00:00<?, ?it/s]

  0%|          | 0/60 [00:00<?, ?it/s]

  0%|          | 0/8 [00:00<?, ?it/s]

In [ ]:
y_true = conversion_classes_num(y_true,convert,reverse_conv=True)
y_pred = conversion_classes_num(y_pred,convert,reverse_conv=True)
report = classification_report(y_true,y_pred)

/usr/local/lib/python3.7/dist-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [ ]:
print(report)

                precision    recall  f1-score   support

      attribué       0.00      0.00      0.00         2
          cité       0.44      0.43      0.44        46
pris en charge       0.89      0.90      0.90       253

      accuracy                           0.82       301
     macro avg       0.45      0.45      0.45       301
  weighted avg       0.82      0.82      0.82       301

